![header](../figures/logos_partenaires._cmems_se.jpg)


<div class="alert alert-block alert-success">
<h1><center>Demo: Create and save mp4 movies of SWOT data  </center></h1></div>

***
**Authors:**  Datlas, IGE, IMEDEA & CLS <br>
**Copyright:** 2022 Datlas, IGE, IMEDEA & CLS <br>
**License:** MIT

In [1]:
import os
import glob
import sys
sys.path.append('..')
import numpy as np 
import xarray as xr 
import matplotlib.pyplot as plt
from datetime import datetime
import glob 

from src import mod_plot
from src import mod_switchvar
from src.dict_regions_info import *

In [2]:

region_info = RegionInfo('GS_info').region_info   # Region dictionary info from dict_regions_info.py


<div class="alert alert-info" role="alert">

<h2>1. Read from regional data file </h2>

</div>
 

In [23]:
path_data = '../denoised_data/SWOT_L3_LR_SSH_Expert_v03_GS_gomezfilt.nc' 
   

ds_passes = xr.open_mfdataset(path_data,combine='nested',concat_dim='num_lines')
ds_passes

<xarray.Dataset>
Dimensions:               (num_lines: 81480, num_pixels: 69)
Coordinates:
    latitude              (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    longitude             (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
Dimensions without coordinates: num_lines, num_pixels
Data variables: (12/22)
    time                  (num_lines, num_pixels) datetime64[ns] dask.array<chunksize=(81480, 69), meta=np.ndarray>
    mdt                   (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ssha                  (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ssha_noiseless        (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ssha_unedited         (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    quality_flag          (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ...                    ...
    duacs_xac             (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    longitude_nadir       (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    latitude_nadir        (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ssha_unetgomezfilt    (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    new_var_name          (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
    ssha_gomez            (num_lines, num_pixels) float64 dask.array<chunksize=(81480, 69), meta=np.ndarray>
Attributes: (12/41)
    contact:                         aviso@altimetry.fr
    creator_email:                   aviso@altimetry.fr
    creator_name:                    DUACS - Data Unification and Altimeter C...
    creator_url:                     https://aviso.altimetry.fr
    institution:                     CNES
    license:                         https://www.aviso.altimetry.fr/fileadmin...
    ...                              ...
    time_coverage_begin:             2023-04-23T17:58:31Z
    time_coverage_end:               2023-04-23T18:49:36Z
    geospatial_lat_min:              -78.272196
    geospatial_lat_max:              78.272247
    geospatial_lon_min:              8.4e-05
    geospatial_lon_max:              359.999504

<div class="alert alert-info" role="alert">

<h2>2. Create SSH movie </h2>

</div> 

In [25]:
mod_plot.movie_intercomp(ds_passes, methods=['Noisy','Denoised V0.3','Gomez'], var_type='ssh', name_var=['ssha','ssha_noiseless','ssha_gomez'],date=np.datetime64('2023-03-29'), dir_output='../figures/',
                    region='Gulfstream', suffix='v03', framerate=3, colsize = 14)

<div class="alert alert-info" role="alert">

<h2>3. Compute SSH gradients and Laplacian </h2>

</div>
 

In [26]:
grad_noisy, lapl_noisy = mod_switchvar.deriv1and2(ds_passes.ssha)
grad_unetgomezfilt, lapl_unetgomezfilt = mod_switchvar.deriv1and2(ds_passes.ssha_noiseless)  
grad_gomezfilt, lapl_gomezfilt = mod_switchvar.deriv1and2(ds_passes.ssha_gomez)  

ds_passes = ds_passes.assign(grad_noisy=lambda ds_passes: ds_passes.ssha * 0 + grad_noisy) 
ds_passes = ds_passes.assign(grad_unetgomezfilt=lambda ds_passes: ds_passes.ssha_noiseless * 0 + grad_unetgomezfilt)
ds_passes = ds_passes.assign(grad_gomezfilt=lambda ds_passes: ds_passes.ssha_gomez * 0 + grad_gomezfilt) 

ds_passes = ds_passes.assign(lapl_noisy=lambda ds_passes: ds_passes.ssha * 0 + lapl_noisy) 
ds_passes = ds_passes.assign(lapl_unetgomezfilt=lambda ds_passes: ds_passes.ssha_noiseless * 0 + lapl_unetgomezfilt)
ds_passes = ds_passes.assign(lapl_gomezfilt=lambda ds_passes: ds_passes.ssha_gomez * 0 + lapl_gomezfilt)


<div class="alert alert-info" role="alert">

<h2>4. Create SSH gradients and Laplacian movies </h2>

</div>
 

In [28]:
mod_plot.movie_intercomp(ds_passes, methods=['Noisy','Denoised V0.3', 'Gomez'], var_type='grad', name_var=['grad_noisy','grad_unetgomezfilt','grad_gomezfilt'], dir_output='../figures/',
                    region='Gulfstream', suffix='v03', framerate=3, colsize = 14)

In [29]:
mod_plot.movie_intercomp(ds_passes, methods=['Noisy','Denoised V0.3', 'Gomez'], var_type='lapl', name_var=['lapl_noisy','lapl_unetgomezfilt','lapl_gomezfilt'], dir_output='../figures/',
                    region='Gulfstream', suffix='v03', framerate=3, colsize = 14)